# Pointwise
* predict the relevance scores

# Import

In [1]:
from collections import Counter
import numpy as np  
import pandas as pd 
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt 
from sklearn.preprocessing import scale 
from sklearn import preprocessing
from sklearn.preprocessing import StandardScaler 
from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error
from sklearn.linear_model import LogisticRegression
from sklearn.utils import shuffle

# models
from sklearn.metrics import mean_squared_error
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn import svm
from sklearn.naive_bayes import GaussianNB
from lightgbm import LGBMRanker

import warnings
warnings.filterwarnings("ignore")

In [2]:
RANDOM_STATE = 24

In [3]:
# 導入資料
train_df = pd.read_pickle('/home/adam/Steph_C/my_thesis/data/Train_by_postoal_code_without_review_pointwise_v2_2.pkl')
test_df = pd.read_pickle('/home/adam/Steph_C/my_thesis/data/Test_by_postoal_code_without_review_pointwise_v2_2.pkl')

In [4]:
train_df = train_df.reset_index(drop=True)
test_df = test_df.reset_index(drop=True)

In [5]:
len(Counter(train_df.name))

1053

In [6]:
train_df.shape

(15636, 27)

In [7]:
test_df.shape

(8391, 27)

In [8]:
# # expr. 1 change relevance score to binary
# # change_rel_score = lambda df: 1 if df['relevance']>0 else 0
# def change_rel_score(df):
#     for i in range(len(df)):
#         if df.relevance[i] > 0 :
#             df.relevance[i]=1
#         else:
#             pass
    
#     return df
# train_df = change_rel_score(train_df)
# test_df = change_rel_score(test_df)

# Models

In [9]:
def _precision(predictions , actuals, k = None):
    
    """
    Calculate the precision at k
    
    Returns: a list of precisions
    """
    
    precisions =[]

    
    for i in range(len(predictions)):
        
        prediction = predictions[i]

        if  k != None:
            prediction =  predictions[i][:k]
#             print(f"prediction: {prediction}")
        
#         print(f"actuals: {actuals}")
        score = 0
        for j in prediction:
            if j in actuals[i]:
                score+=1
        
        print(f"Score(分子):{score}")
        print(f"len(prediction)(分母):{len(prediction)}")
        
        p_score = score/len(prediction) if len(prediction)!=0 else 0
        precisions.append(p_score)
    return precisions
    

def _recall(predictions , actuals, k = None):
    
    """
    Calculate the precision at k
    
    Returns: a list of recalls
    """
    recalls =[]
    
    for i in range(len(predictions)):
        
        prediction =  predictions[i]
        
        if  k != None:
            prediction =  predictions[i][:k]
        
        score = 0
        for j in range(len(prediction)):
            if prediction[j] in actuals[i]:
                score+=1
        recalls.append(score/len(actuals[i]))
    
    return recalls



In [10]:
def calculate_mrr(predictions, actuals):
    """
    Calculate the mean reciprocal rank (MRR) for a set of predictions and actual values.
    
    Parameters:
    predictions (list of lists): A list of predicted rankings sorted by probability.
    actual (list of lists): A list of actual rankings sorted by relevance.
    
    Returns:    
    float: A list of MRR scores.
    """
    mrr_list = []
    for i in range(len(predictions)):
        reciprocal_rank = 0
        if actuals[i][0] in predictions[i]:
            reciprocal_rank = 1/(predictions[i].index(actuals[i][0]) + 1)
        mrr_list.append(reciprocal_rank)
    return mrr_list

In [11]:
def calculate_map( predictions , actuals, k=None):
    """
    Calculate the mean average precision (MAP) for a set of queries.

    Parameters:
    actual (list of sets or lists): A list of sets or lists of the actual relevant items for each query.
    predicted (list of lists): A list of lists of predicted items for each query.
    k (int): The maximum number of predicted items to consider for each query.

    Returns:
    float: A list of MAP scores.
    """
    
    map_list = []
    

    for i in range(len(predictions)):
        
        ap_list = []
        hit = 0 
        cnt = 0 
        
        prediction =  predictions[i]
        
        if k != None:
            prediction =  predictions[i][:k]
        
        
        for j in prediction:
            if j in actuals[i]:
                hit+=1
                cnt+=1
                ap_list.append(hit/cnt)
            else:
                cnt+=1
        map_list.append(np.mean(ap_list))
    
    return map_list
                

In [12]:
def calculate_dcg_ndcg( predictions , actuals, rel ,k=None):
    """
    Calculate the DCG@k , NDCG@k for a set of queries.

    Parameters:
    actual (list of sets or lists): A list of sets or lists of the actual relevant items for each query.
    predicted (list of lists): A list of lists of predicted items for each query.
    k (int): The maximum number of predicted items to consider for each query.

    Returns:
    float: A list of DCG , NDCG scores.
    """
    dcg_list = []
    ndcg_list = []
    
    for i in range(len(predictions)):
        dcg =0
        idcg =0
        
        prediction = predictions[i]
        
        if k != None:
            prediction = predictions[i][:k]
        
        for j in range(len(actuals[i])):
            if actuals[i][j] in prediction:
                rank = prediction.index(actuals[i][j]) + 1
                dcg += np.divide(float(rel[i][j]),np.log2(rank+1))
                idcg += np.divide(float(rel[i][j]),np.log2((j+1)+1))
        dcg_list.append(dcg)
        if np.divide(dcg,idcg) > 1:
            print(rel[i], prediction,actuals[i]  )
            print(i,dcg,idcg  , 'Wrong !!!')
        ndcg_list.append(np.divide(dcg,idcg))
        
    return dcg_list , ndcg_list

In [34]:
# create list of list for query ranking
def get_ranking(df ):
    
    """
    Turn the probability array into a list of lists for calculation.
    
    Parameters:
    df(DataFrame): the test dataframe
    
    Returns:
    prediction (list of lists): A list of predicted rankings for each query.
    actual (list of lists): A list of actual rankings for each query.
    """
 
    pred_list = []
    pred_rel = []
    true_list = []
    
    
    for res in Counter(df.name):
        
        tmp = df[df.name == res]
        a_sorted = tmp.sort_values(by=['relevance'],ascending=[False])
        print(f"a_sorted:\n {a_sorted[['business_id', 'name', 'relevance']]}")
        p_sorted = tmp.sort_values(by=['predictions'],ascending=[False])
        p_sorted = p_sorted[p_sorted.predictions>0]
        print(f"p_sorted:\n {p_sorted[['business_id', 'name', 'predictions']]}")

        true_list.append(list(a_sorted[a_sorted.relevance!=0].postal_code))
        pred_list.append(list(p_sorted.postal_code))
        pred_rel.append(list(a_sorted[a_sorted.relevance!=0].relevance))
        
    return pred_list, pred_rel , true_list

# Model

In [35]:
# models
LR = LogisticRegression(random_state=RANDOM_STATE)
RF = RandomForestClassifier(random_state=RANDOM_STATE)
DTC = DecisionTreeClassifier(random_state=RANDOM_STATE)
KNC = KNeighborsClassifier()
SVC = svm.SVC(random_state=RANDOM_STATE)
GNB = GaussianNB()
LGBM = LGBMRanker(objective="lambdarank",random_state=RANDOM_STATE)

train_features=['density', 'entropy', 'competitiveness','area_pop', 'accessibility','complementary']

get_group_size = lambda df: df.reset_index().groupby("name")['name'].count()

train_groups = get_group_size(train_df).to_numpy()
test_groups = get_group_size(test_df).to_numpy()

print(sum(train_groups) , sum(test_groups))

15636 8391


In [36]:
counts = train_df[['relevance']].value_counts()
counts

relevance
0.0          13852
11.0           588
12.0           556
10.0           251
9.0            125
8.0             87
7.0             55
6.0             34
5.0             31
4.0             23
2.0             14
3.0             13
1.0              7
dtype: int64

In [37]:
log_model = LogisticRegression(solver='lbfgs', max_iter=1000)

In [38]:
train_df = shuffle(train_df, random_state=RANDOM_STATE)
test_df = shuffle(test_df, random_state=RANDOM_STATE)

models = [LR, RF, DTC, KNC, SVC, GNB]
model_name =['LR', 'RF', 'DTC', 'KNC', 'SVC', 'GNB']
score_dict = {}

for i in range(len(models)):
    score_dict[model_name[i]]={}
    model = models[i]
    # Train
    if model_name[i] != 'LGBMRanker':
        model.fit(train_df[train_features].values, train_df[['relevance']].values.ravel())
    else:
        model.fit(train_df[train_features].values, train_df[['relevance']].values.ravel(), group=train_groups)
    
    # Predict
#     print("前：", test_df.head(10))
    predict = model.predict(test_df[train_features].values)
#     print(f"predict:{predict[:20]}")
#     print(f"actual:{test_df[['relevance']].values.ravel()[:20]}")
    test_df['predictions'] = predict
#     print("-"*20)
#     print("後：", test_df.head(10))
    pred_list, pred_rel , true_list = get_ranking(test_df)

    # Evaluation
    mrr_list = calculate_mrr(pred_list , true_list)
    map_list = calculate_map(pred_list , true_list)
    dcg_list , ndcg_list = calculate_dcg_ndcg(pred_list , true_list,pred_rel)
    precision_list_1 = _precision(pred_list , true_list, k=1)
    recall_list_1 = _recall(pred_list , true_list, k=1)
    precision_list_3 = _precision(pred_list , true_list, k=3)
    recall_list_3 = _recall(pred_list , true_list,k=3)
    precision_list = _precision(pred_list , true_list)
    recall_list = _recall(pred_list , true_list)

    score_dict[model_name[i]]['precision @ 1'] = np.mean(precision_list_1)
    score_dict[model_name[i]]['recall @ 1'] = np.mean(recall_list_1)
    score_dict[model_name[i]]['precision @ 3 '] = np.mean(precision_list_3)
    score_dict[model_name[i]]['recall @ 3'] = np.mean(recall_list_3)
    score_dict[model_name[i]]['precision'] = np.mean(precision_list)
    score_dict[model_name[i]]['recall'] = np.mean(recall_list)
    score_dict[model_name[i]]['mrr'] = np.mean(mrr_list)
    score_dict[model_name[i]]['map'] = np.mean(map_list)
    score_dict[model_name[i]]['dcg'] = np.mean(dcg_list)
    score_dict[model_name[i]]['ndcg'] = np.mean(ndcg_list)

a_sorted:
                  business_id                               name  relevance
5278  5qWdftveruKnOJ9FKXcGcA  Fogo de Chao Brazilian Steakhouse       12.0
5280  5hAUdFPi1QFJJOlFReVexg  Fogo de Chao Brazilian Steakhouse        0.0
5281  5hAUdFPi1QFJJOlFReVexg  Fogo de Chao Brazilian Steakhouse        0.0
5285  5hAUdFPi1QFJJOlFReVexg  Fogo de Chao Brazilian Steakhouse        0.0
5284  5hAUdFPi1QFJJOlFReVexg  Fogo de Chao Brazilian Steakhouse        0.0
5283  5hAUdFPi1QFJJOlFReVexg  Fogo de Chao Brazilian Steakhouse        0.0
5282  5hAUdFPi1QFJJOlFReVexg  Fogo de Chao Brazilian Steakhouse        0.0
5279  5hAUdFPi1QFJJOlFReVexg  Fogo de Chao Brazilian Steakhouse        0.0
p_sorted:
 Empty DataFrame
Columns: [business_id, name, predictions]
Index: []
a_sorted:
                  business_id              name  relevance
4137  Fyw7Nszsz2E6ZKy7gjPtDw  The Garden Table       12.0
4144  -HjH9XFJ8lS5Mq-uTsR4OQ  The Garden Table        0.0
4139  -HjH9XFJ8lS5Mq-uTsR4OQ  The Garden Table    

5422  eT69uFkxdxdFOEsX-gbUCQ  Pizza World        0.0
p_sorted:
 Empty DataFrame
Columns: [business_id, name, predictions]
Index: []
a_sorted:
                  business_id                 name  relevance
5167  Rag7H_6BDv9SBoMZxLqD-w  Ten Asian Food Hall       11.0
5171  HAUzjmv7YWHulWLsgdgmIw  Ten Asian Food Hall        0.0
5169  HAUzjmv7YWHulWLsgdgmIw  Ten Asian Food Hall        0.0
5170  HAUzjmv7YWHulWLsgdgmIw  Ten Asian Food Hall        0.0
5173  HAUzjmv7YWHulWLsgdgmIw  Ten Asian Food Hall        0.0
5174  HAUzjmv7YWHulWLsgdgmIw  Ten Asian Food Hall        0.0
5172  HAUzjmv7YWHulWLsgdgmIw  Ten Asian Food Hall        0.0
5168  HAUzjmv7YWHulWLsgdgmIw  Ten Asian Food Hall        0.0
p_sorted:
 Empty DataFrame
Columns: [business_id, name, predictions]
Index: []
a_sorted:
                  business_id                             name  relevance
3955  hDBnGZ40GSYc63GxEmjWVg  Noble Roman's Craft Pizza & Pub       11.0
3954  7-5eljD7oqIdLYU5_sqpqA  Noble Roman's Craft Pizza & Pub       10.0

3965  dgm6jrUZj-vAWa1OU5rbNQ  Yiro Yiro        0.0
p_sorted:
 Empty DataFrame
Columns: [business_id, name, predictions]
Index: []
a_sorted:
                  business_id             name  relevance
2070  UaUWlQpiwn4cpjes-RQeTg  Hibachi Express       10.0
2069  AEAW8IkEQv8wV6lXKfx06w  Hibachi Express        8.0
2075  kfNv-JZpuN6TVNSO6hHdkw  Hibachi Express        0.0
2074  kfNv-JZpuN6TVNSO6hHdkw  Hibachi Express        0.0
2077  kfNv-JZpuN6TVNSO6hHdkw  Hibachi Express        0.0
2071  kfNv-JZpuN6TVNSO6hHdkw  Hibachi Express        0.0
2076  kfNv-JZpuN6TVNSO6hHdkw  Hibachi Express        0.0
2072  kfNv-JZpuN6TVNSO6hHdkw  Hibachi Express        0.0
2073  kfNv-JZpuN6TVNSO6hHdkw  Hibachi Express        0.0
p_sorted:
 Empty DataFrame
Columns: [business_id, name, predictions]
Index: []
a_sorted:
                  business_id                    name  relevance
5890  gtOVX8hGKKIryQs0lGPt3w  Bawarchi Biryani Point       12.0
5891  6UyNeDQWiqt4GvVsRU1aEQ  Bawarchi Biryani Point        0.0
5896  6

Index: []
a_sorted:
                  business_id          name  relevance
2305  VSLgzs_x3mc7Mg8DaqsmfA  Caffe Torino       12.0
2309  tuDmwyx080IEpHsV78tC5A  Caffe Torino        0.0
2312  tuDmwyx080IEpHsV78tC5A  Caffe Torino        0.0
2311  tuDmwyx080IEpHsV78tC5A  Caffe Torino        0.0
2308  tuDmwyx080IEpHsV78tC5A  Caffe Torino        0.0
2307  tuDmwyx080IEpHsV78tC5A  Caffe Torino        0.0
2310  tuDmwyx080IEpHsV78tC5A  Caffe Torino        0.0
2306  tuDmwyx080IEpHsV78tC5A  Caffe Torino        0.0
p_sorted:
 Empty DataFrame
Columns: [business_id, name, predictions]
Index: []
a_sorted:
                  business_id                           name  relevance
1411  qma1sGQv7ArUtzuUTQElRg  Katie's Pizza & Pasta Osteria       12.0
1414  C6KP0hSutumHzLDCFyjvJQ  Katie's Pizza & Pasta Osteria        0.0
1418  C6KP0hSutumHzLDCFyjvJQ  Katie's Pizza & Pasta Osteria        0.0
1413  C6KP0hSutumHzLDCFyjvJQ  Katie's Pizza & Pasta Osteria        0.0
1416  C6KP0hSutumHzLDCFyjvJQ  Katie's Pizza & Pa

Index: []
a_sorted:
                  business_id          name  relevance
7036  fqkEU1N-Q4Yxa1wbXRGpEw  Thai Kitchen       11.0
7040  55ve4cBxbUH0r-EcWnBrCQ  Thai Kitchen        0.0
7037  55ve4cBxbUH0r-EcWnBrCQ  Thai Kitchen        0.0
7039  55ve4cBxbUH0r-EcWnBrCQ  Thai Kitchen        0.0
7038  55ve4cBxbUH0r-EcWnBrCQ  Thai Kitchen        0.0
7042  55ve4cBxbUH0r-EcWnBrCQ  Thai Kitchen        0.0
7043  55ve4cBxbUH0r-EcWnBrCQ  Thai Kitchen        0.0
7041  55ve4cBxbUH0r-EcWnBrCQ  Thai Kitchen        0.0
p_sorted:
 Empty DataFrame
Columns: [business_id, name, predictions]
Index: []
a_sorted:
                  business_id              name  relevance
4042  5vzKjTIICELUoQsLhl_MeA  Greek's Pizzeria       12.0
4043  oage7vZHEIACcK0BAD5ZhA  Greek's Pizzeria       11.0
4041  -BlhrfAM9jUF0nTMd_2FTQ  Greek's Pizzeria        7.0
4044  AKQLvWa6TCsoUhZ7OXo4Mw  Greek's Pizzeria        0.0
4047  AKQLvWa6TCsoUhZ7OXo4Mw  Greek's Pizzeria        0.0
4050  AKQLvWa6TCsoUhZ7OXo4Mw  Greek's Pizzeria        0

...

Index: []
a_sorted:
                  business_id                      name  relevance
1198  BiBwdFcG0ynK50_g7zJTOg  Chopt Creative Salad Co.       12.0
1204  vpHso5Rw346lqdahJCzaow  Chopt Creative Salad Co.        0.0
1201  vpHso5Rw346lqdahJCzaow  Chopt Creative Salad Co.        0.0
1202  vpHso5Rw346lqdahJCzaow  Chopt Creative Salad Co.        0.0
1199  vpHso5Rw346lqdahJCzaow  Chopt Creative Salad Co.        0.0
1203  vpHso5Rw346lqdahJCzaow  Chopt Creative Salad Co.        0.0
1205  vpHso5Rw346lqdahJCzaow  Chopt Creative Salad Co.        0.0
1200  vpHso5Rw346lqdahJCzaow  Chopt Creative Salad Co.        0.0
p_sorted:
 Empty DataFrame
Columns: [business_id, name, predictions]
Index: []
a_sorted:
                  business_id              name  relevance
3847  P_QAD4_iMgqTaWd5On_n3g  TAP Thai Cuisine       11.0
3849  TeUEijNG9w8m2fNaE7J1TA  TAP Thai Cuisine        0.0
3848  TeUEijNG9w8m2fNaE7J1TA  TAP Thai Cuisine        0.0
3850  TeUEijNG9w8m2fNaE7J1TA  TAP Thai Cuisine        0.0
p_sor

a_sorted:
                 business_id                       name  relevance
230  jmwasbZfgj3honf79qKsnA  Street- Taco and Beer Co.       12.0
235  kz1y_1ToM0m4hyQE5p0Uqw  Street- Taco and Beer Co.        0.0
231  kz1y_1ToM0m4hyQE5p0Uqw  Street- Taco and Beer Co.        0.0
237  kz1y_1ToM0m4hyQE5p0Uqw  Street- Taco and Beer Co.        0.0
233  kz1y_1ToM0m4hyQE5p0Uqw  Street- Taco and Beer Co.        0.0
236  kz1y_1ToM0m4hyQE5p0Uqw  Street- Taco and Beer Co.        0.0
232  kz1y_1ToM0m4hyQE5p0Uqw  Street- Taco and Beer Co.        0.0
234  kz1y_1ToM0m4hyQE5p0Uqw  Street- Taco and Beer Co.        0.0
p_sorted:
                 business_id                       name  predictions
231  kz1y_1ToM0m4hyQE5p0Uqw  Street- Taco and Beer Co.         11.0
236  kz1y_1ToM0m4hyQE5p0Uqw  Street- Taco and Beer Co.         11.0
a_sorted:
                  business_id                 name  relevance
1651  CPXc2AorgYR1uxPopLC79A  Portillo's Hot Dogs       12.0
1650  1Tb7ION52mf2I7wXJY9HAw  Portillo's Hot Do

3068  G8H-8KnMFjS4bHtTBX9t7A  Hibachi Buffet         11.0
a_sorted:
                  business_id            name  relevance
1806  QjKVhT6W04-HiDy6XCvn1A  Jon Smith Subs       12.0
1810  2quqM0ajKfTC_DV8sLAvxQ  Jon Smith Subs        0.0
1807  2quqM0ajKfTC_DV8sLAvxQ  Jon Smith Subs        0.0
1808  2quqM0ajKfTC_DV8sLAvxQ  Jon Smith Subs        0.0
1809  2quqM0ajKfTC_DV8sLAvxQ  Jon Smith Subs        0.0
1811  2quqM0ajKfTC_DV8sLAvxQ  Jon Smith Subs        0.0
p_sorted:
 Empty DataFrame
Columns: [business_id, name, predictions]
Index: []
a_sorted:
                  business_id                 name  relevance
6289  sxhU1NUGDYRmp2TtlTLreQ  Taqueria Don Julios       12.0
6293  ZgbB7jSGP_MJZgHpoiGujQ  Taqueria Don Julios        0.0
6296  ZgbB7jSGP_MJZgHpoiGujQ  Taqueria Don Julios        0.0
6291  ZgbB7jSGP_MJZgHpoiGujQ  Taqueria Don Julios        0.0
6295  ZgbB7jSGP_MJZgHpoiGujQ  Taqueria Don Julios        0.0
6294  ZgbB7jSGP_MJZgHpoiGujQ  Taqueria Don Julios        0.0
6292  ZgbB7jSGP_MJZgHp

a_sorted:
                  business_id                       name  relevance
1529  -ebwX4cjBDsZtPnvW1M_BA  The Old Spaghetti Factory       11.0
1536  -ebwX4cjBDsZtPnvW1M_BA  The Old Spaghetti Factory        0.0
1535  -ebwX4cjBDsZtPnvW1M_BA  The Old Spaghetti Factory        0.0
1531  -ebwX4cjBDsZtPnvW1M_BA  The Old Spaghetti Factory        0.0
1534  -ebwX4cjBDsZtPnvW1M_BA  The Old Spaghetti Factory        0.0
1532  -ebwX4cjBDsZtPnvW1M_BA  The Old Spaghetti Factory        0.0
1533  -ebwX4cjBDsZtPnvW1M_BA  The Old Spaghetti Factory        0.0
1530  -ebwX4cjBDsZtPnvW1M_BA  The Old Spaghetti Factory        0.0
p_sorted:
 Empty DataFrame
Columns: [business_id, name, predictions]
Index: []
a_sorted:
                  business_id             name  relevance
6813  eub4YPzxUWWtJoy_d72rSA  Monical's Pizza       12.0
6820  lSfdDzqxFIYmJDWCh3dj_w  Monical's Pizza        0.0
6819  lSfdDzqxFIYmJDWCh3dj_w  Monical's Pizza        0.0
6818  lSfdDzqxFIYmJDWCh3dj_w  Monical's Pizza        0.0
6815  lSfdD

Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):1
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):1
len(prediction)(分母):1
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):1
Score(分子):0
len(prediction)(分母):0
Score(分子):1
len(prediction)(分母):1
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):1
len(prediction)(分母):1
Score(分子):0
len(prediction)(分母):1
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):0
len(prediction)(分母):0
Score(分子):1
le

# Evaluation

In [39]:
pd.DataFrame(score_dict).round(3)

LR     RF    DTC    KNC    SVC    GNB
precision @ 1   0.048  0.429  0.412  0.365  0.045  0.260
recall @ 1      0.037  0.361  0.349  0.307  0.036  0.212
precision @ 3   0.049  0.466  0.463  0.417  0.045  0.261
recall @ 3      0.040  0.509  0.505  0.433  0.036  0.255
precision       0.049  0.467  0.464  0.417  0.045  0.260
recall          0.040  0.513  0.506  0.434  0.036  0.260
mrr             0.038  0.428  0.419  0.369  0.034  0.230
map               NaN    NaN    NaN    NaN    NaN    NaN
dcg             0.536  5.982  5.846  5.094  0.476  3.290
ndcg              NaN    NaN    NaN    NaN    NaN    NaN